# Capstone Project - The Battle of the Neighborhoods (Week 2)
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)



## Introduction: Business Problem <a name="introduction"></a>

Los Angeles is a one of the biggest cities in the US and as a result spans over a huge area with hundreds of neighborhoods. As a result business owners, specially not from LA, can struggle a lot in how to make business decisions on where the location of their businnesses could be most optimally located and as a result may make suboptimal location decisions which result in a negative impact or even failure in their venture. As a result if the information on rent price of living in a neighbourhood as well as the venues located in a neighborhood could be correlated then spending/income ratios could be obtained with an insight of the venues that are mos frequent around that neighborhood. As a result, the businesses can make more optimal decisions to where they open their new venues by knowing the rent price of a neighborhood.

The target audience for this data exploration would be focused mainly on business owners that are interested in creating new venues where the insight to this business problem would increase their revenue/business and decrease the risk of failure or negative results in opening one or more venues. A secondary audience could be people renting houses to get insights of how based on rent prices of a neighborhood the venues in that location could shape up and allow the renters to use that insight to make a better choice in their rent location.

## Data <a name="data"></a>

To tackle the business problem the data will have certain requirements. The first requirement of the data is to choose a city to make this exploration of data. Once a city has been chosen, data of neighborhoods will be needed: which will be name of neighborhood and the latitude and longitude of the neighborhood. Then, for as many neighborhoods as possible, data will be obtained for the most recent obtainable median or average rent price of each neighborhood. Once this is obtained these two data sets gathered will be merged, leaving out all neighborhoods that do not contain rent price data and averaging any neighborhood that contains more than one rent data for the neighborhood. Once this has been done, the Four quare location can be obtained and using the latitude and longitude the top 5-10 venues can be obtained and this data merged to the previous data. Now the data is ready to be evaluated and analyzed.

For this data I will use the city of LA.

In [1]:
import pandas as pd
import numpy as np
import math
import re

In [2]:
# The code was removed by Watson Studio for sharing.

Here I will obtain the data for LA Neighborhoods

In [59]:
body = client_d8120f4c44654c8492bb144395d3c2f2.get_object(Bucket='applieddatasciencecapstoneibmcour-donotdelete-pr-tokjk722xvsf4y',Key='la_neighborhoods.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

df_la_neigh = pd.read_csv(body)
df_la_neigh.head()

set             slug  \
0  L.A. County Neighborhoods (Current)            acton   
1  L.A. County Neighborhoods (Current)  adams-normandie   
2  L.A. County Neighborhoods (Current)     agoura-hills   
3  L.A. County Neighborhoods (Current)       agua-dulce   
4  L.A. County Neighborhoods (Current)         alhambra   

                                            the_geom  \
0  MULTIPOLYGON (((-118.20261747920541 34.5389897...   
1  MULTIPOLYGON (((-118.30900800000012 34.0374109...   
2  MULTIPOLYGON (((-118.76192500000009 34.1682029...   
3  MULTIPOLYGON (((-118.2546773959221 34.55830403...   
4  MULTIPOLYGON (((-118.12174700000014 34.1050399...   

                                 kind       external_i             name  \
0  L.A. County Neighborhood (Current)            acton            Acton   
1  L.A. County Neighborhood (Current)  adams-normandie  Adams-Normandie   
2  L.A. County Neighborhood (Current)     agoura-hills     Agoura Hills   
3  L.A. County Neighborhood (Current)       agua-dulce       Agua Dulce   
4  L.A. County Neighborhood (Current)         alhambra         Alhambra   

                                          display_na       sqmi  \
0           Acton L.A. County Neighborhood (Current)  39.339109   
1  Adams-Normandie L.A. County Neighborhood (Curr...   0.805350   
2    Agoura Hills L.A. County Neighborhood (Current)   8.146760   
3      Agua Dulce L.A. County Neighborhood (Current)  31.462632   
4        Alhambra L.A. County Neighborhood (Current)   7.623814   

                  type  name_1  slug_1    latitude  longitude  \
0  unincorporated-area     NaN     NaN -118.169810  34.497355   
1    segment-of-a-city     NaN     NaN -118.300208  34.031461   
2      standalone-city     NaN     NaN -118.759885  34.146736   
3  unincorporated-area     NaN     NaN -118.317104  34.504927   
4      standalone-city     NaN     NaN -118.136512  34.085539   

                                        location  
0  POINT(34.497355239240846 -118.16981019229348)  
1  POINT(34.031461499124156 -118.30020800000011)  
2  POINT(34.146736499122795 -118.75988450000015)  
3   POINT(34.504926999796837 -118.3171036690717)  
4  POINT(34.085538999123571 -118.13651200000021)

All the unique neighborhoods from the data set are the following

In [60]:
df_la_neigh['name'].unique()

array(['Acton', 'Adams-Normandie', 'Agoura Hills', 'Agua Dulce',
       'Alhambra', 'Alondra Park', 'Artesia', 'Altadena', 'Angeles Crest',
       'Arcadia', 'Arleta', 'Arlington Heights', 'Athens',
       'Atwater Village', 'Avalon', 'Avocado Heights', 'Azusa',
       'Vermont-Slauson', 'Baldwin Hills/Crenshaw', 'Baldwin Park',
       'Bel-Air', 'Bellflower', 'Bell Gardens', 'Green Valley', 'Bell',
       'Beverly Crest', 'Beverly Grove', 'Burbank', 'Koreatown',
       'Beverly Hills', 'Beverlywood', 'Boyle Heights', 'Bradbury',
       'Brentwood', 'Broadway-Manchester', 'Calabasas', 'Canoga Park',
       'Carson', 'Carthay', 'Castaic Canyons', 'Chatsworth', 'Castaic',
       'Central-Alameda', 'Century City', 'Cerritos', 'Charter Oak',
       'Chatsworth Reservoir', 'Chesterfield Square', 'Cheviot Hills',
       'Chinatown', 'Citrus', 'Claremont', 'Northridge', 'Commerce',
       'Compton', 'Cypress Park', 'La Mirada', 'Covina', 'Cudahy',
       'Culver City', 'Del Aire', 'Del Rey', 

trim the data columns for all the necessary information

In [61]:
la_neigh_col_list = ['name', 'sqmi', 'type', 'latitude', 'longitude', 'the_geom', 'location']
df_la_neigh = df_la_neigh[la_neigh_col_list]
df_la_neigh.head()

name       sqmi                 type    latitude  longitude  \
0            Acton  39.339109  unincorporated-area -118.169810  34.497355   
1  Adams-Normandie   0.805350    segment-of-a-city -118.300208  34.031461   
2     Agoura Hills   8.146760      standalone-city -118.759885  34.146736   
3       Agua Dulce  31.462632  unincorporated-area -118.317104  34.504927   
4         Alhambra   7.623814      standalone-city -118.136512  34.085539   

                                            the_geom  \
0  MULTIPOLYGON (((-118.20261747920541 34.5389897...   
1  MULTIPOLYGON (((-118.30900800000012 34.0374109...   
2  MULTIPOLYGON (((-118.76192500000009 34.1682029...   
3  MULTIPOLYGON (((-118.2546773959221 34.55830403...   
4  MULTIPOLYGON (((-118.12174700000014 34.1050399...   

                                        location  
0  POINT(34.497355239240846 -118.16981019229348)  
1  POINT(34.031461499124156 -118.30020800000011)  
2  POINT(34.146736499122795 -118.75988450000015)  
3   POINT(34.504926999796837 -118.3171036690717)  
4  POINT(34.085538999123571 -118.13651200000021)

In [62]:
df_la_neigh['type'].unique()

array(['unincorporated-area', 'segment-of-a-city', 'standalone-city'],
      dtype=object)

Slightly modify the data into easier format to process later on with foursquare

In [63]:
df_neigh_loc = df_la_neigh.loc[:, ['name', 'latitude', 'longitude']]
df_neigh_loc['Location'] = df_neigh_loc.apply(lambda x: str((x['longitude'], x['latitude'])), axis=1)
print(type(df_neigh_loc['Location'][0]))
df_neigh_loc = df_neigh_loc[['name', 'latitude', 'longitude', 'Location']]

df_neigh_loc.rename(columns={"name": "Neighborhood", 'latitude': 'Longitude', 'longitude': 'Latitude' }, inplace=True)
# df_neigh_loc.sort_values(by='Location')
df_neigh_loc

<class 'str'>


Neighborhood   Longitude   Latitude  \
0                                    Acton -118.169810  34.497355   
1                          Adams-Normandie -118.300208  34.031461   
2                             Agoura Hills -118.759885  34.146736   
3                               Agua Dulce -118.317104  34.504927   
4                                 Alhambra -118.136512  34.085539   
5                             Alondra Park -118.335156  33.889617   
6                                  Artesia -118.080101  33.866896   
7                                 Altadena -118.136239  34.193871   
8                            Angeles Crest -117.922395  34.313937   
9                                  Arcadia -118.030419  34.133230   
10                                  Arleta -118.430757  34.243100   
11                       Arlington Heights -118.323408  34.044910   
12                                  Athens -118.304656  33.923693   
13                         Atwater Village -118.262373  34.131066   
14                                  Avalon -118.327332  33.336954   
15                         Avocado Heights -118.001261  34.040881   
16                                   Azusa -117.912469  34.137470   
17                         Vermont-Slauson -118.290358  33.983914   
18                  Baldwin Hills/Crenshaw -118.357746  34.011970   
19                            Baldwin Park -117.975191  34.081109   
20                                 Bel-Air -118.458416  34.102057   
21                              Bellflower -118.129032  33.888013   
22                            Bell Gardens -118.149936  33.965686   
23                            Green Valley -118.414217  34.620007   
24                                    Bell -118.179166  33.981161   
25                           Beverly Crest -118.423263  34.106007   
26                           Beverly Grove -118.376102  34.076633   
27                                 Burbank -118.325211  34.182010   
28                               Koreatown -118.304958  34.064510   
29                           Beverly Hills -118.399534  34.082544   
30                             Beverlywood -118.393982  34.043510   
31                           Boyle Heights -118.210788  34.039168   
32                                Bradbury -117.968574  34.154240   
33                               Brentwood -118.492189  34.086241   
34                     Broadway-Manchester -118.275352  33.941224   
35                               Calabasas -118.671632  34.136254   
36                             Canoga Park -118.601519  34.210855   
37                                  Carson -118.248010  33.839520   
38                                 Carthay -118.368910  34.057856   
39                         Castaic Canyons -118.454769  34.564146   
40                              Chatsworth -118.612354  34.256403   
41                                 Castaic -118.633349  34.481750   
42                         Central-Alameda -118.247213  34.006864   
43                            Century City -118.415083  34.055326   
44                                Cerritos -118.068638  33.866892   
45                             Charter Oak -117.857520  34.100075   
46                    Chatsworth Reservoir -118.626953  34.233072   
47                     Chesterfield Square -118.313208  33.983763   
48                           Cheviot Hills -118.411462  34.040853   
49                               Chinatown -118.237006  34.063510   
50                                  Citrus -117.892164  34.116180   
51                               Claremont -117.718769  34.122365   
52                              Northridge -118.527969  34.238805   
53                                Commerce -118.157363  33.995079   
54                                 Compton -118.221810  33.893252   
55                            Cypress Park -118.224157  34.092139   
56                               La Mirada -118.007221  33.900794   
57                          

In [64]:
def locStr_to_tuple(loc_str):
    return tuple(map(float, list(filter(None, re.split('[; \(\), ]', loc_str)))))
    

Get the data of rent price in neighborhood which will be LA median rent price. Also I will select the most recent rent data, so for 2016 from this data set

In [65]:
# https://usc.data.socrata.com/Los-Angeles/Rent-Price-LA-/4a97-v5tx

body = client_d8120f4c44654c8492bb144395d3c2f2.get_object(Bucket='applieddatasciencecapstoneibmcour-donotdelete-pr-tokjk722xvsf4y',Key='Rent_Price__LA_.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

df_la_rent = pd.read_csv(body)
print(df_la_rent.shape)
df_la_rent = df_la_rent[df_la_rent['Year'] == 2016]
print(df_la_rent.shape)
df_la_rent.dropna(inplace=True)
print(df_la_rent.shape)
la_rent_col = ['Year', 'Amount', 'Neighborhood']
df_la_rent = df_la_rent[la_rent_col].reset_index()
df_la_rent.rename(columns={"Amount": "Median Rent Price"}, inplace=True)
df_la_rent.drop(columns=['index', 'Year'], inplace=True)
df_la_rent.sort_values('Neighborhood').head(10)

(16390, 12)
(2344, 12)
(2296, 12)


Median Rent Price     Neighborhood
2244             1500.0            Acton
297               965.0  Adams-Normandie
1908             1093.0  Adams-Normandie
1674              928.0  Adams-Normandie
2146              885.0  Adams-Normandie
1507             1050.0  Adams-Normandie
1733             2232.0     Agoura Hills
1682             3321.0     Agoura Hills
675              1911.0     Agoura Hills
1033             1188.0         Alhambra

For the neighborhoods with more than one entry, take the mean

In [66]:
df_la_rent = df_la_rent.groupby(by='Neighborhood').mean()
df_la_rent.head()

Median Rent Price
Neighborhood                      
Acton                      1500.00
Adams-Normandie             984.20
Agoura Hills               2488.00
Alhambra                   1245.75
Alondra Park               1484.00

The highest 5 average median rent Neighborhoods in LA are the following

In [67]:
df_la_rent.sort_values('Median Rent Price', ascending=False).head(5)

Median Rent Price
Neighborhood                           
San Marino                       3500.0
Rolling Hills                    3500.0
Beverlywood                      3463.0
Malibu                           3202.0
Palos Verdes Estates             2930.0

The lowest 5 average median rent Neighborhoods in LA are the following

In [68]:
df_la_rent.sort_values('Median Rent Price', ascending=True).head(5)

Median Rent Price
Neighborhood                                     
Vernon                                      625.0
Elysian Park                                686.0
Unincorporated Catalina Island              870.0
Pico-Union                                  918.5
Harvard Park                                923.0

In [70]:
df_la_rent.reset_index(level=0, inplace=True)
print('max is ' + str(df_la_rent['Median Rent Price'].max()) + ' and min is ' + str(df_la_rent['Median Rent Price'].min()))
df_la_rent['Median Rent Price'] = 10 * df_la_rent['Median Rent Price'] / (df_la_rent['Median Rent Price'].max())
print('max is ' + str(df_la_rent['Median Rent Price'].max()) + ' and min is ' + str(df_la_rent['Median Rent Price'].min()))
df_la_rent

max is 3500.0 and min is 625.0
max is 10.0 and min is 1.7857142857142858


index                           Neighborhood  Median Rent Price
0        0                                  Acton           4.285714
1        1                        Adams-Normandie           2.812000
2        2                           Agoura Hills           7.108571
3        3                               Alhambra           3.559286
4        4                           Alondra Park           4.240000
5        5                               Altadena           4.298214
6        6                          Angeles Crest           3.608571
7        7                                Arcadia           4.209351
8        8                                 Arleta           4.651905
9        9                      Arlington Heights           3.114286
10      10                                Artesia           4.022857
11      11                                 Athens           2.817143
12      12                        Atwater Village           4.083810
13      13                                 Avalon           4.074286
14      14                        Avocado Heights           3.770000
15      15                                  Azusa           3.796000
16      16                 Baldwin Hills/Crenshaw           3.031837
17      17                           Baldwin Park           3.604107
18      18                                Bel-Air           5.797143
19      19                                   Bell           2.984898
20      20                           Bell Gardens           3.227302
21      21                             Bellflower           3.462222
22      22                          Beverly Crest           6.822857
23      23                          Beverly Grove           5.156786
24      24                          Beverly Hills           6.644082
25      25                            Beverlywood           9.894286
26      26                          Boyle Heights           2.814171
27      27                               Bradbury           6.571429
28      28                              Brentwood           6.560000
29      29                    Broadway-Manchester           3.224000
30      30                                Burbank           4.405217
31      31                              Calabasas           7.298095
32      32                            Canoga Park           3.958242
33      33                                 Carson           4.193534
34      34                                Carthay           5.085714
35      35                                Castaic           7.203810
36      36                        Castaic Canyons           5.318730
37      37                        Central-Alameda           2.794000
38      38                           Century City           6.777143
39      39                               Cerritos           6.590130
40      40                            Charter Oak           4.157143
41      41                             Chatsworth           5.491688
42      42                   Chatsworth Reservoir           4.157143
43      43                    Chesterfield Square           3.349524
44      44                          Cheviot Hills           7.364286
45      45                              Chinatown           3.534286
46      46                                 Citrus           3.748571
47      47                              Claremont           4.658571
48      48                               Commerce           2.782857
49      49                                Compton           3.216429
50      50                                 Covina           3.999143
51      51                                 Cudahy           3.291429
52      52                            Culver City           4.515102
53      53                           Cypress Park           2.908571
54      54                               Del Aire           3.658571
55      55                                Del Rey           4.724898
56      56                            Diamond Bar           5.437460
57 

Compare both data sets and combine the data

In [71]:
# get a set of the neighbourhood names in both data sets

set_all_rent_neigh = set(np.sort(df_la_rent['Neighborhood'].unique()))
set_all_neigh = set(df_la_neigh['name'].unique())

inter_neigh = set_all_neigh.intersection(set_all_rent_neigh)

print('All neighs in LA contains ' + str(len(set_all_neigh)) + ' values and rent neighs in LA contains ' + str(len(set_all_rent_neigh)) + ' values.')
print('Amount that intersect are ' + str(len(inter_neigh)) + ' values')

if len(set_all_rent_neigh) == len(inter_neigh):
    print( 'Rent neighbourhoods are all included in All LA neighbourhoods data' )

All neighs in LA contains 272 values and rent neighs in LA contains 257 values.
Amount that intersect are 257 values
Rent neighbourhoods are all included in All LA neighbourhoods data


In [72]:
# MERGE DATA
merge_la_col_order = ['Neighborhood', 'Longitude', 'Latitude', 'Median Rent Price']
la_merged_data = pd.merge(df_neigh_loc, df_la_rent, on='Neighborhood')[merge_la_col_order]
print(la_merged_data.describe())
la_merged_data.head()

        Longitude    Latitude  Median Rent Price
count  257.000000  257.000000         257.000000
mean  -118.262893   34.075176           4.331686
std      0.205698    0.187897           1.425139
min   -118.822912   33.336954           1.785714
25%   -118.393982   33.975324           3.337857
50%   -118.290358   34.057856           3.960635
75%   -118.131791   34.139387           4.930714
max   -117.718769   34.725569          10.000000


Neighborhood   Longitude   Latitude  Median Rent Price
0            Acton -118.169810  34.497355           4.285714
1  Adams-Normandie -118.300208  34.031461           2.812000
2     Agoura Hills -118.759885  34.146736           7.108571
3         Alhambra -118.136512  34.085539           3.559286
4     Alondra Park -118.335156  33.889617           4.240000

### Get Location Data from FourSquare

In [17]:
!conda install -c conda-forge folium=0.5.0 --yes

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    altair-4.0.0               |             py_0         606 KB  conda-forge
    certifi-2019.11.28         |           py36_0         149 KB  conda-forge
    folium-0.5.0               |             py_0          45 KB  conda-forge
    openssl-1.1.1d             |       h516909a_0         2.1 MB  conda-forge
    branca-0.3.1               |             py_0          25 KB  conda-forge
    ca-certificates-2019.11.28 |       hecc5488_0         145 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         3.1 MB

The following NEW packages will be 

In [73]:
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests

getting a map of LA and the filtered data

In [74]:
address = 'Los Angeles, California'

geolocator = Nominatim(user_agent="la_explorer_v2")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of LA are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of LA are 34.0536909, -118.2427666.


In [75]:
# create map of Manhattan using latitude and longitude values
map_la = folium.Map(location=[latitude, longitude], zoom_start=9)

# add markers to map
for lat, lng, label in zip(la_merged_data['Latitude'], la_merged_data['Longitude'], la_merged_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_la)  
    
map_la

Getting the FourSquare Stuff going

In [76]:
CLIENT_ID = '2UEJBBAVL0HB5VD5KXMN345NWOTASPJV5L0F3HPFK1WXTPCW' # your Foursquare ID
CLIENT_SECRET = 'TWBGVCK1SCNPQCZULXMRYHWOLWWQPRHX3H3DT05JQD5BH0DA' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

#print('Your credentails:')
#print('CLIENT_ID: ' + CLIENT_ID)
#print('CLIENT_SECRET:' + CLIENT_SECRET)

In [77]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [78]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

getting all the venues for the wanted LA data

In [79]:
# get nearby venues
la_venues = getNearbyVenues(names= la_merged_data['Neighborhood'], latitudes= la_merged_data['Latitude'],
                            longitudes= la_merged_data['Longitude'], radius=800)

print(la_venues.shape)
la_venues.head()

Acton
Adams-Normandie
Agoura Hills
Alhambra
Alondra Park
Artesia
Altadena
Angeles Crest
Arcadia
Arleta
Arlington Heights
Athens
Atwater Village
Avalon
Avocado Heights
Azusa
Vermont-Slauson
Baldwin Hills/Crenshaw
Baldwin Park
Bel-Air
Bellflower
Bell Gardens
Bell
Beverly Crest
Beverly Grove
Burbank
Koreatown
Beverly Hills
Beverlywood
Boyle Heights
Bradbury
Brentwood
Broadway-Manchester
Calabasas
Canoga Park
Carson
Carthay
Castaic Canyons
Chatsworth
Castaic
Central-Alameda
Century City
Cerritos
Charter Oak
Chatsworth Reservoir
Chesterfield Square
Cheviot Hills
Chinatown
Citrus
Claremont
Northridge
Commerce
Compton
Cypress Park
La Mirada
Covina
Cudahy
Culver City
Del Aire
Del Rey
Diamond Bar
Downey
Downtown
Duarte
Eagle Rock
East Compton
East Hollywood
East La Mirada
Elizabeth Lake
East Los Angeles
East Pasadena
East San Gabriel
Echo Park
El Monte
El Segundo
El Sereno
Elysian Park
Elysian Valley
Vermont Square
Encino
Exposition Park
Fairfax
Florence-Firestone
Florence
Gardena
Glassell Park

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0            Acton              34.497355             -118.169810   
1            Acton              34.497355             -118.169810   
2  Adams-Normandie              34.031461             -118.300208   
3  Adams-Normandie              34.031461             -118.300208   
4  Adams-Normandie              34.031461             -118.300208   

                Venue  Venue Latitude  Venue Longitude  \
0    Epik Engineering       34.498718      -118.168046   
1  Alma Gardening Co.       34.494762      -118.172550   
2   Orange Door Sushi       34.032485      -118.299368   
3      Revolutionario       34.025417      -118.298582   
4       Ignatius Cafe       34.031772      -118.293006   

               Venue Category  
0  Construction & Landscaping  
1  Construction & Landscaping  
2            Sushi Restaurant  
3                  Taco Place  
4                        Café

In [80]:
print(la_venues.groupby('Neighborhood').count().describe())
la_venues.groupby('Neighborhood').count()

       Neighborhood Latitude  Neighborhood Longitude       Venue  \
count             247.000000              247.000000  247.000000   
mean               25.817814               25.817814   25.817814   
std                25.162787               25.162787   25.162787   
min                 1.000000                1.000000    1.000000   
25%                 6.000000                6.000000    6.000000   
50%                16.000000               16.000000   16.000000   
75%                38.000000               38.000000   38.000000   
max               100.000000              100.000000  100.000000   

       Venue Latitude  Venue Longitude  Venue Category  
count      247.000000       247.000000      247.000000  
mean        25.817814        25.817814       25.817814  
std         25.162787        25.162787       25.162787  
min          1.000000         1.000000        1.000000  
25%          6.000000         6.000000        6.000000  
50%         16.000000        16.000000       

Neighborhood Latitude  \
Neighborhood                                                   
Acton                                                      2   
Adams-Normandie                                           14   
Agoura Hills                                              54   
Alhambra                                                  21   
Alondra Park                                               5   
Altadena                                                  15   
Arcadia                                                   46   
Arleta                                                     5   
Arlington Heights                                         41   
Artesia                                                   68   
Athens                                                     5   
Atwater Village                                           55   
Avalon                                                    34   
Avocado Heights                                           14   
Azusa                                                     25   
Baldwin Hills/Crenshaw                                     7   
Baldwin Park                                              22   
Bel-Air                                                    4   
Bell                                                      22   
Bell Gardens                                              17   
Bellflower                                                39   
Beverly Crest                                              2   
Beverly Grove                                            100   
Beverly Hills                                              7   
Beverlywood                                               10   
Boyle Heights                                             45   
Bradbury                                                   2   
Brentwood                                                  3   
Broadway-Manchester                                        5   
Burbank                                                   61   
Calabasas                                                  1   
Canoga Park                                               21   
Carson                                                     1   
Carthay                                                   68   
Central-Alameda                                            9   
Century City                                             100   
Cerritos                                                  30   
Charter Oak                                               13   
Chatsworth                                                13   
Chesterfield Square                                       30   
Cheviot Hills                                             15   
Chinatown                                                 86   
Citrus                                                     8   
Claremont                                                  1   
Commerce                                                  15   
Compton                                                   27   
Covina                                                    39   
Cudahy                                                    21   
Culver City                                               58   
Cypress Park                                              11   
Del Aire                                                  16   
Del Rey                                                   26   
Diamond Bar                                               51   
Downey                                                    64   
Downtown                                                 100   
Duarte                                                     1   
Eagle Rock                                                40   
East Compton                                              10   
East Hollywood                                            64   
East La Mirada                                            16   
East Los Angeles                                          30   
East Pa

In [81]:
print('There are {} uniques categories.'.format(len(la_venues['Venue Category'].unique())))

There are 385 uniques categories.


## Methodology <a name="methodology"></a>

Firstly, I obtain the needed data which 3 different data sets. The first data set is the one containing LA neighborhood basic info. The second one is the most recent rent price data for all available LA neighborhoods. The third one is the location data, so data of venues, for each neighborhood location.

Once these data sets are obtained they are combined and modified to make it ready to analyze. The first thing to do is to obtain a one hot encoding of all the neighborhoods for each neighborhood. Secondly, the fequency is obtained for each type of venue obtained for each neighborhood. Finally, the top venues, in terms of frequency, are obtained and made into columns to analyze with the mean median rent price for each neighborhood.

After this, this data will be analyzed using a machine learning k-cluster machine learning algorithm to figure out how this data can be categorized and clustered to obtain insights on the business problem proposed in the beginning.

## Analysis <a name="analysis"></a>

Analyzing neighbourhoods

In [82]:
# one hot encoding
la_onehot = pd.get_dummies(la_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
la_onehot['Neighborhood'] = la_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = list(la_onehot.columns[:])
n_index = fixed_columns.index('Neighborhood')
fixed_columns.insert(0, fixed_columns.pop(n_index))
la_onehot = la_onehot[fixed_columns]

la_onehot.head()

Neighborhood  ATM  Accessories Store  Adult Boutique  Airport  \
0            Acton    0                  0               0        0   
1            Acton    0                  0               0        0   
2  Adams-Normandie    0                  0               0        0   
3  Adams-Normandie    0                  0               0        0   
4  Adams-Normandie    0                  0               0        0   

   Airport Terminal  Alternative Healer  American Restaurant  Antique Shop  \
0                 0                   0                    0             0   
1                 0                   0                    0             0   
2                 0                   0                    0             0   
3                 0                   0                    0             0   
4                 0                   0                    0             0   

   Arcade  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                       0            0           0   
1       0                       0            0           0   
2       0                       0            0           0   
3       0                       0            0           0   
4       0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  Astrologer  \
0                    0                     0                 0           0   
1                    0                     0                 0           0   
2                    0                     0                 0           0   
3                    0                     0                 0           0   
4                    0                     0                 0           0   

   Athletics & Sports  Australian Restaurant  Auto Dealership  Auto Garage  \
0                   0                      0                0            0   
1                   0                      0                0            0   
2                   0                      0                0            0   
3                   0                      0                0            0   
4                   0                      0                0            0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0              0                0          0           0           0       0   
1              0                0          0           0           0       0   
2              0                0          0           0           0       0   
3              0                0          0           0           0       0   
4              0                0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0     0    0               0                 0                 0   
1     0    0               0                 0                 0   
2     0    0               0                 0                 0   
3     0    0               0                 0                 0   
4     0    0               0                 0                 0   

   Bathing Area  Beach  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0             0      0                0         0            0           0   
1             0      0                0         0            0           0   
2             0      0                0         0            0           0   
3             0      0                0         0            0           0   
4             0      0                0         0            0           0   

   Big Box Store  Bistro  Board Shop  Boat or Ferry  Bookstore  \
0              0       0           0              0          0   
1              0       0           0              0          0   
2              0       0           0              0          0   
3              0       0           0              0          0   
4              0       0           0              0          0   

   Botanical Garden  Boutique  Bowling Alle

In [83]:
la_onehot.shape

(6377, 385)

In [84]:
# TODO : STANDARDIZE OR LOWER THE IMPACT OF MEDIAN RENT PRICE?

la_grouped = la_onehot.groupby('Neighborhood').mean().reset_index()
print(la_grouped.shape)
la_grouped = pd.merge(la_merged_data[['Neighborhood', 'Median Rent Price']], la_grouped, on='Neighborhood')
print(la_grouped.shape)
la_grouped

(247, 385)
(247, 386)


Neighborhood  Median Rent Price       ATM  \
0                                    Acton           4.285714  0.000000   
1                          Adams-Normandie           2.812000  0.000000   
2                             Agoura Hills           7.108571  0.018519   
3                                 Alhambra           3.559286  0.000000   
4                             Alondra Park           4.240000  0.000000   
5                                  Artesia           4.022857  0.000000   
6                                 Altadena           4.298214  0.000000   
7                                  Arcadia           4.209351  0.000000   
8                                   Arleta           4.651905  0.000000   
9                        Arlington Heights           3.114286  0.000000   
10                                  Athens           2.817143  0.000000   
11                         Atwater Village           4.083810  0.018182   
12                                  Avalon           4.074286  0.000000   
13                         Avocado Heights           3.770000  0.000000   
14                                   Azusa           3.796000  0.000000   
15                         Vermont-Slauson           2.809643  0.000000   
16                  Baldwin Hills/Crenshaw           3.031837  0.000000   
17                            Baldwin Park           3.604107  0.000000   
18                                 Bel-Air           5.797143  0.000000   
19                              Bellflower           3.462222  0.000000   
20                            Bell Gardens           3.227302  0.058824   
21                                    Bell           2.984898  0.000000   
22                           Beverly Crest           6.822857  0.000000   
23                           Beverly Grove           5.156786  0.000000   
24                                 Burbank           4.405217  0.000000   
25                               Koreatown           3.048374  0.000000   
26                           Beverly Hills           6.644082  0.000000   
27                             Beverlywood           9.894286  0.000000   
28                           Boyle Heights           2.814171  0.022222   
29                                Bradbury           6.571429  0.000000   
30                               Brentwood           6.560000  0.000000   
31                     Broadway-Manchester           3.224000  0.000000   
32                               Calabasas           7.298095  0.000000   
33                             Canoga Park           3.958242  0.000000   
34                                  Carson           4.193534  0.000000   
35                                 Carthay           5.085714  0.000000   
36                              Chatsworth           5.491688  0.000000   
37                         Central-Alameda           2.794000  0.000000   
38                            Century City           6.777143  0.000000   
39                                Cerritos           6.590130  0.000000   
40                             Charter Oak           4.157143  0.000000   
41                     Chesterfield Square           3.349524  0.000000   
42                           Cheviot Hills           7.364286  0.000000   
43                               Chinatown           3.534286  0.000000   
44                                  Citrus           3.748571  0.000000   
45                               Claremont           4.658571  0.000000   
46                              Northridge           4.529592  0.000000   
47                                Commerce           2.782857  0.000000   
48                                 Compton           3.216429  0.000000   
49                            Cypress Park           2.908571  0.000000   
50                               La Mirada           4.499714  0.000000   
51                                  Covina           3.999143  0.000000   
52                                  Cudahy           3.

showing the top 5 venues for each neighbourhood

In [85]:
num_top_venues = 5

for hood in la_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = la_grouped[la_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[2:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Acton----
                           venue  freq
0     Construction & Landscaping   1.0
1                            ATM   0.0
2                   Noodle House   0.0
3                           Park   0.0
4  Paper / Office Supplies Store   0.0


----Adams-Normandie----
                  venue  freq
0          Burger Joint  0.14
1            Playground  0.07
2        Farmers Market  0.07
3  Fast Food Restaurant  0.07
4            Taco Place  0.07


----Agoura Hills----
                  venue  freq
0  Fast Food Restaurant  0.09
1    Chinese Restaurant  0.06
2    Mexican Restaurant  0.06
3         Deli / Bodega  0.06
4              Pharmacy  0.04


----Alhambra----
                 venue  freq
0    Convenience Store  0.19
1          Pizza Place  0.10
2  Sporting Goods Shop  0.05
3       Breakfast Spot  0.05
4  Dumpling Restaurant  0.05


----Alondra Park----
                venue  freq
0                Park   0.2
1          Hookah Bar   0.2
2      Breakfast Spot   0.2
3  Mexican Rest

In [86]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[2:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

getting a df of the top 10 most common venues with the neighbourhood column to the far left

In [87]:
num_top_venues = 5

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = la_grouped['Neighborhood']

for ind in np.arange(la_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(la_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood       1st Most Common Venue 2nd Most Common Venue  \
0            Acton  Construction & Landscaping           Yoga Studio   
1  Adams-Normandie                Burger Joint           Gas Station   
2     Agoura Hills        Fast Food Restaurant    Chinese Restaurant   
3         Alhambra           Convenience Store           Pizza Place   
4     Alondra Park                  Hookah Bar                  Park   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
0           Event Space             Drugstore           Dry Cleaner  
1        Farmers Market            Taco Place                  Café  
2    Mexican Restaurant         Deli / Bodega                   Gym  
3   Sporting Goods Shop       Auto Dealership   Rental Car Location  
4        Breakfast Spot    Mexican Restaurant      Asian Restaurant

In [88]:
neighborhoods_venues_sorted

Neighborhood       1st Most Common Venue  \
0                                    Acton  Construction & Landscaping   
1                          Adams-Normandie                Burger Joint   
2                             Agoura Hills        Fast Food Restaurant   
3                                 Alhambra           Convenience Store   
4                             Alondra Park                  Hookah Bar   
5                                  Artesia           Indian Restaurant   
6                                 Altadena              Scenic Lookout   
7                                  Arcadia             Bubble Tea Shop   
8                                   Arleta           Convenience Store   
9                        Arlington Heights          Mexican Restaurant   
10                                  Athens                       Hotel   
11                         Atwater Village        Fast Food Restaurant   
12                                  Avalon                       Hotel   
13                         Avocado Heights          Mexican Restaurant   
14                                   Azusa                 Coffee Shop   
15                         Vermont-Slauson        Fast Food Restaurant   
16                  Baldwin Hills/Crenshaw         American Restaurant   
17                            Baldwin Park          Mexican Restaurant   
18                                 Bel-Air                      Bakery   
19                              Bellflower                 Pizza Place   
20                            Bell Gardens                Burger Joint   
21                                    Bell                        Park   
22                           Beverly Crest                   Juice Bar   
23                           Beverly Grove              Clothing Store   
24                                 Burbank        Fast Food Restaurant   
25                               Koreatown           Korean Restaurant   
26                           Beverly Hills               Women's Store   
27                             Beverlywood                    Boutique   
28                           Boyle Heights          Mexican Restaurant   
29                                Bradbury                     Stables   
30                               Brentwood                       Trail   
31                     Broadway-Manchester                       Hotel   
32                               Calabasas                Tennis Court   
33                             Canoga Park          Mexican Restaurant   
34                                  Carson                        Park   
35                                 Carthay        Ethiopian Restaurant   
36                              Chatsworth                        Park   
37                         Central-Alameda                  Taco Place   
38                            Century City                  Food Truck   
39                                Cerritos           Korean Restaurant   
40                             Charter Oak                Liquor Store   
41                     Chesterfield Square                 Pizza Place   
42                           Cheviot Hills              Baseball Field   
43                               Chinatown          Chinese Restaurant   
44                                  Citrus                Home Service   
45                               Claremont  Construction & Landscaping   
46                              Northridge                 Pizza Place   
47                                Commerce        Fast Food Restaurant   
48                                 Compton        Fast Food Restaurant   
49                            Cypress Park          Mexican Restaurant   
50                               La Mirada        Fast Food Restaurant   
51                                  Covina          Mexican Restaurant   
52                                  Cudahy        Fast Food Restaurant   
53                             Cul

Cluster neighbourhoods while changing cluster labels to int type, renaming a column to make it easier when merging and removing any unwanted rows, one row had nan values.

In [89]:
kclusters = 5

la_grouped_clustering = la_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(la_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 0, 1, 0, 2, 2, 2, 2, 2, 0], dtype=int32)

In [90]:

# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

la_merged = la_merged_data

#la_merged.rename(columns={"Neighbourhood": "Neighborhood"}, inplace=True)

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
la_merged = pd.merge(la_merged_data, neighborhoods_venues_sorted, on='Neighborhood')
la_merged.dropna(inplace=True)
la_merged.reset_index(drop=True, inplace=True)

la_merged.head() 

Neighborhood   Longitude   Latitude  Median Rent Price  Cluster Labels  \
0            Acton -118.169810  34.497355           4.285714               2   
1  Adams-Normandie -118.300208  34.031461           2.812000               0   
2     Agoura Hills -118.759885  34.146736           7.108571               1   
3         Alhambra -118.136512  34.085539           3.559286               0   
4     Alondra Park -118.335156  33.889617           4.240000               2   

        1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0  Construction & Landscaping           Yoga Studio           Event Space   
1                Burger Joint           Gas Station        Farmers Market   
2        Fast Food Restaurant    Chinese Restaurant    Mexican Restaurant   
3           Convenience Store           Pizza Place   Sporting Goods Shop   
4                  Hookah Bar                  Park        Breakfast Spot   

  4th Most Common Venue 5th Most Common Venue  
0             Drugstore           Dry Cleaner  
1            Taco Place                  Café  
2         Deli / Bodega                   Gym  
3       Auto Dealership   Rental Car Location  
4    Mexican Restaurant      Asian Restaurant

In [91]:
la_merged['Cluster Labels'] = la_merged['Cluster Labels'].astype('int64') 

la_merged

Neighborhood   Longitude   Latitude  \
0                                    Acton -118.169810  34.497355   
1                          Adams-Normandie -118.300208  34.031461   
2                             Agoura Hills -118.759885  34.146736   
3                                 Alhambra -118.136512  34.085539   
4                             Alondra Park -118.335156  33.889617   
5                                  Artesia -118.080101  33.866896   
6                                 Altadena -118.136239  34.193871   
7                                  Arcadia -118.030419  34.133230   
8                                   Arleta -118.430757  34.243100   
9                        Arlington Heights -118.323408  34.044910   
10                                  Athens -118.304656  33.923693   
11                         Atwater Village -118.262373  34.131066   
12                                  Avalon -118.327332  33.336954   
13                         Avocado Heights -118.001261  34.040881   
14                                   Azusa -117.912469  34.137470   
15                         Vermont-Slauson -118.290358  33.983914   
16                  Baldwin Hills/Crenshaw -118.357746  34.011970   
17                            Baldwin Park -117.975191  34.081109   
18                                 Bel-Air -118.458416  34.102057   
19                              Bellflower -118.129032  33.888013   
20                            Bell Gardens -118.149936  33.965686   
21                                    Bell -118.179166  33.981161   
22                           Beverly Crest -118.423263  34.106007   
23                           Beverly Grove -118.376102  34.076633   
24                                 Burbank -118.325211  34.182010   
25                               Koreatown -118.304958  34.064510   
26                           Beverly Hills -118.399534  34.082544   
27                             Beverlywood -118.393982  34.043510   
28                           Boyle Heights -118.210788  34.039168   
29                                Bradbury -117.968574  34.154240   
30                               Brentwood -118.492189  34.086241   
31                     Broadway-Manchester -118.275352  33.941224   
32                               Calabasas -118.671632  34.136254   
33                             Canoga Park -118.601519  34.210855   
34                                  Carson -118.248010  33.839520   
35                                 Carthay -118.368910  34.057856   
36                              Chatsworth -118.612354  34.256403   
37                         Central-Alameda -118.247213  34.006864   
38                            Century City -118.415083  34.055326   
39                                Cerritos -118.068638  33.866892   
40                             Charter Oak -117.857520  34.100075   
41                     Chesterfield Square -118.313208  33.983763   
42                           Cheviot Hills -118.411462  34.040853   
43                               Chinatown -118.237006  34.063510   
44                                  Citrus -117.892164  34.116180   
45                               Claremont -117.718769  34.122365   
46                              Northridge -118.527969  34.238805   
47                                Commerce -118.157363  33.995079   
48                                 Compton -118.221810  33.893252   
49                            Cypress Park -118.224157  34.092139   
50                               La Mirada -118.007221  33.900794   
51                                  Covina -117.883922  34.087495   
52                                  Cudahy -118.185573  33.962620   
53                             Culver City -118.409025  34.005899   
54                                Del Aire -118.369832  33.915552   
55                                 Del Rey -118.423993  33.989292   
56                             Diamond Bar -117.815731  34.000641   
57                          

## Results and Discussion <a name="results"></a>

create a map with the clusters showing

In [92]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=9)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(la_merged['Latitude'], la_merged['Longitude'], la_merged['Neighborhood'], la_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [93]:
# Cluster 1
la_cluster_1 = la_merged.loc[la_merged['Cluster Labels'] == 0, la_merged.columns[[0] + [4] + [3] + list(range(5, la_merged.shape[1]))]]
la_cluster_1

Neighborhood  Cluster Labels  Median Rent Price  \
1           Adams-Normandie               0           2.812000   
3                  Alhambra               0           3.559286   
9         Arlington Heights               0           3.114286   
10                   Athens               0           2.817143   
15          Vermont-Slauson               0           2.809643   
16   Baldwin Hills/Crenshaw               0           3.031837   
17             Baldwin Park               0           3.604107   
19               Bellflower               0           3.462222   
20             Bell Gardens               0           3.227302   
21                     Bell               0           2.984898   
25                Koreatown               0           3.048374   
28            Boyle Heights               0           2.814171   
31      Broadway-Manchester               0           3.224000   
37          Central-Alameda               0           2.794000   
41      Chesterfield Square               0           3.349524   
43                Chinatown               0           3.534286   
47                 Commerce               0           2.782857   
48                  Compton               0           3.216429   
49             Cypress Park               0           2.908571   
52                   Cudahy               0           3.291429   
61             East Compton               0           3.285714   
62           East Hollywood               0           3.032063   
63           East La Mirada               0           3.587143   
64           Elizabeth Lake               0           3.497143   
65         East Los Angeles               0           2.932143   
68                Echo Park               0           3.542540   
69                 El Monte               0           3.269643   
71                El Sereno               0           3.120519   
72             Elysian Park               0           1.960000   
73           Elysian Valley               0           3.461905   
74           Vermont Square               0           3.007619   
76          Exposition Park               0           3.046122   
78       Florence-Firestone               0           2.850549   
79                 Florence               0           3.053626   
80                  Gardena               0           3.506857   
81            Glassell Park               0           3.337857   
82            Green Meadows               0           3.155714   
83            Vermont Vista               0           2.919048   
86            Gramercy Park               0           3.365714   
90              Harbor City               0           3.528571   
91           Harbor Gateway               0           3.082857   
92          Harvard Heights               0           2.938571   
93             Harvard Park               0           2.637143   
94              Walnut Park               0           2.940000   
95         Hawaiian Gardens               0           3.567143   
96                Hawthorne               0           3.407937   
100           Highland Park               0           3.254082   
101  Historic South-Central               0           2.787143   
104               Hollywood               0           3.541688   
105         Huntington Park               0           2.810526   
106               Hyde Park               0           2.958286   
107               Inglewood               0           3.417884   
109          Jefferson Park               0           3.042381   
117        Lake Los Angeles               0           3.005714   
118       Lake View Terrace               0           3.260952   
120               Lancaster               0           3.174603   
121               La Puente               0           3.429643   
122               Larchmont               0           3.564286   
123                   Watts               0           2.857143   
126            Leimert Park               0           3

In [94]:
# Sum of all values in 5 Most Common venues for cluster 1
la_cluster_1.iloc[:, 3].value_counts().add(la_cluster_1.iloc[:, 4].value_counts(), fill_value=0).add(la_cluster_1.iloc[:, 5].value_counts(), fill_value=0).add(la_cluster_1.iloc[:, 6].value_counts(), fill_value=0).add(la_cluster_1.iloc[:, 7].value_counts(), fill_value=0).sort_values(ascending=False)

Mexican Restaurant                 41.0
Fast Food Restaurant               27.0
Pizza Place                        23.0
Grocery Store                      21.0
Convenience Store                  18.0
Park                               16.0
Burger Joint                       15.0
Pharmacy                           14.0
Bakery                             12.0
Café                                9.0
Coffee Shop                         8.0
Mobile Phone Shop                   8.0
Food                                8.0
Taco Place                          8.0
Liquor Store                        8.0
Gas Station                         7.0
Sandwich Place                      7.0
Asian Restaurant                    7.0
Discount Store                      6.0
Donut Shop                          6.0
Video Store                         6.0
Chinese Restaurant                  6.0
Food Truck                          5.0
Construction & Landscaping          4.0
Thai Restaurant                     4.0


In [95]:
# Cluster 2
la_cluster_2 = la_merged.loc[la_merged['Cluster Labels'] == 1, la_merged.columns[[0] + [4] + [3] + list(range(5, la_merged.shape[1]))]]
la_cluster_2

Neighborhood  Cluster Labels  Median Rent Price  \
2                             Agoura Hills               1           7.108571   
22                           Beverly Crest               1           6.822857   
26                           Beverly Hills               1           6.644082   
29                                Bradbury               1           6.571429   
30                               Brentwood               1           6.560000   
32                               Calabasas               1           7.298095   
38                            Century City               1           6.777143   
39                                Cerritos               1           6.590130   
42                           Cheviot Hills               1           7.364286   
111                   La Canada Flintridge               1           6.693571   
115                       La Habra Heights               1           6.097143   
128                           Leona Valley               1           6.125714   
136                        Manhattan Beach               1           6.500357   
137                         Marina del Rey               1           7.357143   
155                      Pacific Palisades               1           7.676667   
169                           Porter Ranch               1           7.652653   
175                  Rolling Hills Estates               1           6.550714   
176                    Rancho Palos Verdes               1           7.541429   
204                        Stevenson Ranch               1           6.717143   
211                                Topanga               1           6.871429   
218  Unincorporated Santa Monica Mountains               1           7.156327   
227                                 Walnut               1           6.242857   
231                             West Hills               1           6.803636   
234                       Westlake Village               1           8.032857   
246                         Woodland Hills               1           6.618681   

    1st Most Common Venue 2nd Most Common Venue    3rd Most Common Venue  \
2    Fast Food Restaurant    Chinese Restaurant       Mexican Restaurant   
22              Juice Bar              Vineyard              Yoga Studio   
26          Women's Store          Dance Studio       Salon / Barbershop   
29                Stables          Home Service            Event Service   
30                  Trail            Food Truck              Yoga Studio   
32           Tennis Court           Yoga Studio              Fish Market   
38             Food Truck           Coffee Shop                     Café   
39      Korean Restaurant     Mobile Phone Shop              Pizza Place   
42         Baseball Field          Tennis Court     Gym / Fitness Center   
111                Bakery           Pizza Place              Yoga Studio   
115                  Park          Home Service     Ethiopian Restaurant   
128     Convenience Store                  Food              Pizza Place   
136                  Bank                 Hotel     Fast Food Restaurant   
137       Harbor / Marina         Boat or Ferry               Restaurant   
155        Pilates Studio                   Gym           Nightlife Spot   
169                  Park           Golf Course                 Pharmacy   
175         Movie Theater                 Trail              Yoga Studio   
176                 Trail       Nature Preserve              Yoga Studio   
204  Gym / Fitness Center      Business Service               Food Truck   
211         Women's Store    Italian Restaurant  Health & Beauty Service   
218                 Trail           Yoga Studio         Doner Restaurant   
227          Soccer Field                  Park           Scenic Lookout   
231                  Park               Theater            Grocery Store   
234                  Lake   American Restaurant               Shoe Store   
246          Concert Ha

In [96]:
# Sum of all values in 5 Most Common venues for cluster 2
la_cluster_2.iloc[:, 3].value_counts().add(la_cluster_2.iloc[:, 4].value_counts(), fill_value=0).add(la_cluster_2.iloc[:, 5].value_counts(), fill_value=0).add(la_cluster_2.iloc[:, 6].value_counts(), fill_value=0).add(la_cluster_2.iloc[:, 7].value_counts(), fill_value=0).sort_values(ascending=False)

Yoga Studio                 10.0
Donut Shop                   8.0
Event Service                5.0
Park                         5.0
Trail                        4.0
Food Truck                   4.0
Gym                          4.0
Gym / Fitness Center         4.0
Pizza Place                  3.0
Drugstore                    3.0
Ethiopian Restaurant         3.0
Mexican Restaurant           3.0
Home Service                 3.0
Restaurant                   2.0
Bakery                       2.0
Fast Food Restaurant         2.0
Sushi Restaurant             2.0
Tennis Court                 2.0
Health & Beauty Service      2.0
Women's Store                2.0
Coffee Shop                  2.0
Italian Restaurant           2.0
Scenic Lookout               1.0
Dongbei Restaurant           1.0
Field                        1.0
Farm                         1.0
Entertainment Service        1.0
Theater                      1.0
Vineyard                     1.0
Deli / Bodega                1.0
Doner Rest

In [97]:
# Cluster 3
la_cluster_3 = la_merged.loc[la_merged['Cluster Labels'] == 2, la_merged.columns[[0] + [4] + [3] + list(range(5, la_merged.shape[1]))]]
la_cluster_3

Neighborhood  Cluster Labels  Median Rent Price  \
0                        Acton               2           4.285714   
4                 Alondra Park               2           4.240000   
5                      Artesia               2           4.022857   
6                     Altadena               2           4.298214   
7                      Arcadia               2           4.209351   
8                       Arleta               2           4.651905   
11             Atwater Village               2           4.083810   
12                      Avalon               2           4.074286   
13             Avocado Heights               2           3.770000   
14                       Azusa               2           3.796000   
24                     Burbank               2           4.405217   
33                 Canoga Park               2           3.958242   
34                      Carson               2           4.193534   
40                 Charter Oak               2           4.157143   
44                      Citrus               2           3.748571   
45                   Claremont               2           4.658571   
46                  Northridge               2           4.529592   
50                   La Mirada               2           4.499714   
51                      Covina               2           3.999143   
53                 Culver City               2           4.515102   
54                    Del Aire               2           3.658571   
57                      Downey               2           3.897013   
58                    Downtown               2           3.648352   
59                      Duarte               2           4.042857   
60                  Eagle Rock               2           3.754643   
66               East Pasadena               2           3.985714   
67            East San Gabriel               2           4.245143   
70                  El Segundo               2           4.680714   
84                    Glendale               2           4.442711   
99                   Mar Vista               2           4.570857   
102            Hollywood Hills               2           4.558571   
108                  Irwindale               2           4.165714   
110                   Industry               2           4.540408   
116                Lake Balboa               2           4.609388   
125                   Lawndale               2           3.852857   
130                     Lomita               2           3.679048   
131                 Long Beach               2           3.647236   
132                  Los Feliz               2           4.068810   
138          Mayflower Village               2           3.892381   
142              Mission Hills               2           4.256571   
145                   Monrovia               2           4.370000   
148           Mount Washington               2           3.839286   
149                North Hills               2           4.185934   
151  Northwest Antelope Valley               2           4.454286   
154                    Norwalk               2           4.017415   
156                    Pacoima               2           3.757594   
159                   Palmdale               2           3.724107   
160                      Palms               2           4.288312   
161                West Carson               2           3.644286   
163                Pico Rivera               2           3.775824   
167                   Pasadena               2           4.647059   
168                     Pomona               2           3.744828   
174                     Reseda               2           3.843516   
177                Rancho Park               2           4.308571   
181           Santa Fe Springs               2           4.051429   
183               San Fernando               2           3.685714   
186                San Gabriel               2           3.960635   
188             

In [98]:
# Sum of all values in 5 Most Common venues for cluster 3
la_cluster_3.iloc[:, 3].value_counts().add(la_cluster_3.iloc[:, 4].value_counts(), fill_value=0).add(la_cluster_3.iloc[:, 5].value_counts(), fill_value=0).add(la_cluster_3.iloc[:, 6].value_counts(), fill_value=0).add(la_cluster_3.iloc[:, 7].value_counts(), fill_value=0).sort_values(ascending=False)

Mexican Restaurant               31.0
Park                             19.0
Pizza Place                      18.0
Fast Food Restaurant             15.0
Coffee Shop                      15.0
Yoga Studio                      11.0
Burger Joint                     10.0
Grocery Store                    10.0
Convenience Store                10.0
Donut Shop                       10.0
Trail                             9.0
Italian Restaurant                7.0
Pharmacy                          6.0
Home Service                      6.0
American Restaurant               6.0
Drugstore                         6.0
Sandwich Place                    6.0
Video Store                       5.0
Chinese Restaurant                5.0
Taco Place                        5.0
Thai Restaurant                   5.0
Asian Restaurant                  5.0
Cosmetics Shop                    4.0
Ice Cream Shop                    4.0
Bar                               4.0
Sushi Restaurant                  4.0
Construction

In [99]:
# Cluster 4
la_cluster_4 = la_merged.loc[la_merged['Cluster Labels'] == 3, la_merged.columns[[0] + [4] + [3] + list(range(5, la_merged.shape[1]))]]
la_cluster_4

Neighborhood  Cluster Labels  Median Rent Price  \
27            Beverlywood               3           9.894286   
134                Malibu               3           9.148571   
157  Palos Verdes Estates               3           8.371429   
178         Rolling Hills               3          10.000000   
187            San Marino               3          10.000000   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
27               Boutique            Bagel Shop        Ice Cream Shop   
134                 Trail               Dog Run           Auto Garage   
157           Gas Station     Convenience Store           Flower Shop   
178           Flower Shop      Business Service    Athletics & Sports   
187                Garden           Art Gallery              Tea Room   

    4th Most Common Venue 5th Most Common Venue  
27                   Park   Empanada Restaurant  
134       Bed & Breakfast             Surf Spot  
157      Botanical Garden             Pet Store  
178           Yoga Studio         Event Service  
187                   Gym   American Restaurant

In [100]:
# Sum of all values in 5 Most Common venues for cluster 4
la_cluster_4.iloc[:, 3].value_counts().add(la_cluster_4.iloc[:, 4].value_counts(), fill_value=0).add(la_cluster_4.iloc[:, 5].value_counts(), fill_value=0).add(la_cluster_4.iloc[:, 6].value_counts(), fill_value=0).add(la_cluster_4.iloc[:, 7].value_counts(), fill_value=0).sort_values(ascending=False)

Flower Shop            2.0
Yoga Studio            1.0
Dog Run                1.0
Art Gallery            1.0
Athletics & Sports     1.0
Auto Garage            1.0
Bagel Shop             1.0
Bed & Breakfast        1.0
Botanical Garden       1.0
Boutique               1.0
Business Service       1.0
Convenience Store      1.0
Empanada Restaurant    1.0
Trail                  1.0
Event Service          1.0
Garden                 1.0
Gas Station            1.0
Gym                    1.0
Ice Cream Shop         1.0
Park                   1.0
Pet Store              1.0
Surf Spot              1.0
Tea Room               1.0
American Restaurant    1.0
dtype: float64

In [101]:
# Cluster 5
la_cluster_5 = la_merged.loc[la_merged['Cluster Labels'] == 4, la_merged.columns[[0] + [4] + [3] + list(range(5, la_merged.shape[1]))]]
la_cluster_5

Neighborhood  Cluster Labels  Median Rent Price  \
18                                 Bel-Air               4           5.797143   
23                           Beverly Grove               4           5.156786   
35                                 Carthay               4           5.085714   
36                              Chatsworth               4           5.491688   
55                                 Del Rey               4           4.724898   
56                             Diamond Bar               4           5.437460   
75                                  Encino               4           5.318701   
77                                 Fairfax               4           4.930714   
85                                Glendora               4           5.111868   
87                           Granada Hills               4           6.020816   
88                        Hacienda Heights               4           5.290989   
89                            Hancock Park               4           5.535238   
97                           Hermosa Beach               4           5.751429   
98                            Hidden Hills               4           5.982857   
103                   Hollywood Hills West               4           5.877857   
112                  La Crescenta-Montrose               4           5.395714   
113                         Ladera Heights               4           5.050714   
114                            Playa Vista               4           5.567143   
119                               Lakewood               4           4.719048   
124                               La Verne               4           4.778776   
141                           Mid-Wilshire               4           4.817143   
153                         North Whittier               4           5.725714   
164                         Pico-Robertson               4           4.883810   
166                          Playa del Rey               4           5.595714   
171                          Redondo Beach               4           5.135824   
172                                 Ramona               4           4.851429   
180                        Rowland Heights               4           5.370857   
182                              San Dimas               4           5.499643   
184                           Santa Monica               4           4.754135   
185                               Sawtelle               4           4.761143   
190                          Santa Clarita               4           4.987805   
191                           Shadow Hills               4           5.675714   
192                           Sherman Oaks               4           4.714958   
193                           Sierra Madre               4           5.062857   
205                            Studio City               4           5.229841   
208                                Tarzana               4           5.691429   
212                               Torrance               4           4.819048   
220                                 Venice               4           5.477143   
221  Unincorporated Santa Susana Mountains               4           5.012857   
228                            Westchester               4           5.154545   
235                       West Los Angeles               4           5.513571   
239                               Westwood               4           5.833810   

        1st Most Common Venue   2nd Most Common Venue  \
18                     Bakery                Dive Bar   
23             Clothing Store               Juice Bar   
35       Ethiopian Restaurant             Pizza Place   
36                       Park       Convenience Store   
55         Mexican Restaurant                  Bakery   
56                Pizza Place      Chinese Restaurant   
75           Sushi Restaurant     Japanese Restaurant   
77                       Café      Italian Restaurant   
85                   Mountain    

In [102]:
# Sum of all values in 5 Most Common venues for cluster 5
la_cluster_5.iloc[:, 3].value_counts().add(la_cluster_5.iloc[:, 4].value_counts(), fill_value=0).add(la_cluster_5.iloc[:, 5].value_counts(), fill_value=0).add(la_cluster_5.iloc[:, 6].value_counts(), fill_value=0).add(la_cluster_5.iloc[:, 7].value_counts(), fill_value=0).sort_values(ascending=False)

Coffee Shop                      12.0
Pizza Place                       9.0
Yoga Studio                       8.0
Mexican Restaurant                8.0
Park                              7.0
Donut Shop                        7.0
Drugstore                         6.0
Event Service                     6.0
Japanese Restaurant               5.0
Sushi Restaurant                  5.0
American Restaurant               5.0
Italian Restaurant                4.0
Hotel                             4.0
Bakery                            4.0
Grocery Store                     4.0
Ethiopian Restaurant              3.0
Juice Bar                         3.0
Gym / Fitness Center              3.0
Gym                               3.0
Food Truck                        3.0
Sandwich Place                    3.0
Doner Restaurant                  3.0
Spa                               3.0
Convenience Store                 3.0
Clothing Store                    3.0
Breakfast Spot                    3.0
Beach       

## Conclusion <a name="conclusion"></a>

The purpose of this experiment was to identify relationships between venues and median rent price, which for these results was standardised to reduce the weight of the numbers in the machine learning model. As to be expected not a clear trend can be seen. But certain key information can be extracted from the different clusters and conclusions. Venues such as pizza place and mexican restaurants can be seen appear in the top 5 venues  more frequently in different clusters with certain rent prices in comparison to venues such as yoga studios and flower shops. More specifically in terms of pizza and mexican restaurants it can be observed to appear more frequently in the bottom half of all rent prices in LA while Yoga studios and flower shops become more frequent for the top half of rent prices.

From these clusters one can analyze the clusters and how frequent certain restaurants are to be able to figure out the tendencies of their specific venue in relation to the neighborhood with specific rent price. Then they can choose which neighborhood they want open one or more venues calculating risk and rewards.